In [31]:
import numpy as np # library to handle data in a vectorized manner
import pandas as pd # library for data analsysis
import json # library to handle JSON files

#!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library

#!conda install -c anaconda beautifulsoup4
import bs4 as bsoup
from bs4 import BeautifulSoup
import requests
#!conda install -c conda-forge geocoder
#import geocoder # import geocoder

Solving environment: done

## Package Plan ##

  environment location: /opt/conda/envs/Python36

  added / updated specs: 
    - folium=0.5.0


The following packages will be downloaded:

    package                    |            build
    ---------------------------|-----------------
    ca-certificates-2019.11.28 |       hecc5488_0         145 KB  conda-forge

The following packages will be UPDATED:

    ca-certificates: 2019.9.11-hecc5488_0 conda-forge --> 2019.11.28-hecc5488_0 conda-forge


ca-certificates-2019 | 145 KB    | ##################################### | 100% 
Preparing transaction: done
Verifying transaction: done
Executing transaction: done


In [32]:
url='http://techslides.com/list-of-countries-and-capitals'
page=requests.get(url)
soup2=BeautifulSoup(page.content, 'html.parser')
table=soup2.find_all('table')[0]
df=pd.read_html(str(table))[0]
df.columns=df.iloc[0]
df=df.drop(df.index[0])
df=df.dropna()
df=df.reset_index(drop=True)
df.head()

0    Country Name Capital Name Capital Latitude Capital Longitude  \
0     Afghanistan        Kabul      34.51666667         69.183333   
1   Aland Islands    Mariehamn        60.116667              19.9   
2         Albania       Tirana      41.31666667         19.816667   
3         Algeria      Algiers            36.75              3.05   
4  American Samoa    Pago Pago     -14.26666667            -170.7   

0 Country Code Continent Name  
0           AF           Asia  
1           AX         Europe  
2           AL         Europe  
3           DZ         Africa  
4           AS      Australia

In [77]:
#CLIENT_ID = 'WXTQZPHF0DVEZSX2JZF1SM2W42IZ4GKYLTDD3NXT5RH5MFC0' # your Foursquare ID
#CLIENT_ID='ASL5M0NEO4SQM5NG555NDSZGE2GTI3WGRF4DUK5XLH0K24WN'
#CLIENT_ID='HFP2NOHQMXSSBDXHKRHDKBOOTCBEGTPA0WFGJTW0GOGRCWWP'
CLIENT_ID='EJPPILEFOTQ3HKQM5K5X2FT4NMLR3R2UIPF03WSVV5WVYFYX'
#CLIENT_ID='KXOMBN54USAZF4B4J034A23UYRBRSDNPP5XTY1PYKX0AE254'
#CLIENT_ID='2MBDRFUDBV1FVDPDXWQYRB0LV0QHGEIESBGYAEQOZ1HEXB1L'
#CLIENT_ID='IIGUMCMVSOOWJILSNOZJKJIO1JV5RBTOQLHW1P4YM30VSIJW'
#CLIENT_SECRET = 'OYJMUIILZBFG0FKRXXV3AQSA0NHH0DBUQ0DMYJKPWWPAINUJ' # your Foursquare Secret
#CLIENT_SECRET='PNJ01DK3SXBQHZ2FCLXJIOY1HDLXZINMZZ3SB4I10HCVEX3I'
#CLIENT_SECRET='WV4J3W1LRITD2HO3ISGKZCOQESCZEM1LHSRMWXA2VQWICH55'
CLIENT_SECRET='U4KHCCZMU4SHX3EEL3QH0CWM5WPNZGWU4XIVA12XHSZ5D14I'
#CLIENT_SECRET='0YIKLUFW3NR5DWFS4U3FMNCM2NRX01OXQISVVWXKZSKF1XNJ'
#CLIENT_SECRET='KA3YYRJ0YK0RURMKXIWIFYBFFUZK1JHBP25OLISYIY55XRT4'
#CLIENT_SECRET='CXYG1KMGCNOI002Q44TGSQPFEVLL40NPLISNGHKRFOYQIWIH'
VERSION = '20180605' # Foursquare API version

In [87]:
LIMIT=500
def getNearbyVenues(names, latitudes, longitudes, radius=2000):
#radius of 2km around the city centre   
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        #print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Capital Name', 
                  'Capital Latitude', 
                  'Capital Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [88]:
df1=df

world_venues = getNearbyVenues(names=df1['Capital Name'],
                                   latitudes=df1['Capital Latitude'],
                                   longitudes=df1['Capital Longitude']
                                  )

world_venues.head()

Capital Name Capital Latitude Capital Longitude                Venue  \
0        Kabul      34.51666667         69.183333   Kabul Serena Hotel   
1        Kabul      34.51666667         69.183333           Ciano ISAF   
2        Kabul      34.51666667         69.183333     Kabul Star Hotel   
3        Kabul      34.51666667         69.183333  Blue Cafe - ISAF HQ   
4        Kabul      34.51666667         69.183333      Gulbahar Center   

   Venue Latitude  Venue Longitude Venue Category  
0       34.520398        69.177970          Hotel  
1       34.528054        69.187925    Pizza Place  
2       34.531202        69.177159          Hotel  
3       34.530122        69.192213    Coffee Shop  
4       34.523273        69.173430  Shopping Mall

In [89]:
# one hot encoding
world_onehot = pd.get_dummies(world_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
world_onehot['Capital Name'] = world_venues['Capital Name'] 

# move neighborhood column to the first column
fixed_columns = [world_onehot.columns[-1]] + list(world_onehot.columns[:-1])
world_onehot = world_onehot[fixed_columns]

world_onehot.head()

Capital Name  ATM  Acai House  Accessories Store  Afghan Restaurant  \
0        Kabul    0           0                  0                  0   
1        Kabul    0           0                  0                  0   
2        Kabul    0           0                  0                  0   
3        Kabul    0           0                  0                  0   
4        Kabul    0           0                  0                  0   

   African Restaurant  Airport  Airport Food Court  Airport Lounge  \
0                   0        0                   0               0   
1                   0        0                   0               0   
2                   0        0                   0               0   
3                   0        0                   0               0   
4                   0        0                   0               0   

   Airport Service  Airport Terminal  American Restaurant  Amphitheater  \
0                0                 0                    0             0   
1                0                 0                    0             0   
2                0                 0                    0             0   
3                0                 0                    0             0   
4                0                 0                    0             0   

   Antique Shop  Arcade  Arepa Restaurant  Argentinian Restaurant  \
0             0       0                 0                       0   
1             0       0                 0                       0   
2             0       0                 0                       0   
3             0       0                 0                       0   
4             0       0                 0                       0   

   Art Gallery  Art Museum  Arts & Crafts Store  Arts & Entertainment  \
0            0           0                    0                     0   
1            0           0                    0                     0   
2            0           0                    0                     0   
3            0           0                    0                     0   
4            0           0                    0                     0   

   Asian Restaurant  Athletics & Sports  Auditorium  Australian Restaurant  \
0                 0                   0           0                      0   
1                 0                   0           0                      0   
2                 0                   0           0                      0   
3                 0                   0           0                      0   
4                 0                   0           0                      0   

   Austrian Restaurant  Auto Dealership  Auto Garage  Auto Workshop  \
0                    0                0            0              0   
1                    0                0            0              0   
2                    0                0            0              0   
3                    0                0            0              0   
4                    0                0            0              0   

   Automotive Shop  BBQ Joint  Baby Store  Bagel Shop  Bakery  Ballroom  Bank  \
0                0          0           0           0       0         0     0   
1                0          0           0           0       0         0     0   
2                0          0           0           0       0         0     0   
3                0          0           0           0       0         0     0   
4                0          0           0           0       0         0     0   

   Bar  Baseball Field  Baseball Stadium  Basketball Court  \
0    0               0                 0                 0   
1    0               0                 0                 0   
2    0               0                 0                 0   
3    0               0                 0                 0   
4    0               0                 0                 0   

   Basketball Stadium  Bath House  Bay  Beach  Beach Bar  Bed & Breakfast  \
0   

In [91]:
world_grouped = world_onehot.groupby('Capital Name').mean().reset_index()
world_grouped

Capital Name       ATM  Acai House  Accessories Store  \
0              Abu Dhabi  0.000000        0.00           0.000000   
1                  Abuja  0.000000        0.00           0.000000   
2                  Accra  0.000000        0.00           0.000000   
3            Addis Ababa  0.000000        0.00           0.000000   
4                Algiers  0.000000        0.00           0.000000   
5                  Amman  0.000000        0.00           0.000000   
6              Amsterdam  0.000000        0.00           0.000000   
7       Andorra la Vella  0.000000        0.00           0.000000   
8                 Ankara  0.000000        0.00           0.000000   
9           Antananarivo  0.000000        0.00           0.000000   
10                  Apia  0.000000        0.00           0.000000   
11              Ashgabat  0.000000        0.00           0.000000   
12                Asmara  0.000000        0.00           0.000000   
13                Astana  0.000000        0.00           0.000000   
14              Asuncion  0.000000        0.00           0.000000   
15                Athens  0.000000        0.00           0.000000   
16                Avarua  0.000000        0.00           0.000000   
17               Baghdad  0.000000        0.00           0.000000   
18                  Baku  0.000000        0.00           0.000000   
19                Bamako  0.000000        0.00           0.000000   
20   Bandar Seri Begawan  0.000000        0.00           0.000000   
21               Bangkok  0.000000        0.00           0.000000   
22                Bangui  0.000000        0.00           0.000000   
23                Banjul  0.000000        0.00           0.000000   
24            Basseterre  0.000000        0.00           0.000000   
25               Beijing  0.000000        0.00           0.000000   
26                Beirut  0.000000        0.00           0.000000   
27              Belgrade  0.000000        0.00           0.000000   
28              Belmopan  0.000000        0.00           0.000000   
29                Berlin  0.000000        0.00           0.000000   
30                  Bern  0.000000        0.00           0.000000   
31               Bishkek  0.000000        0.00           0.000000   
32                Bissau  0.000000        0.00           0.000000   
33                Bogota  0.000000        0.00           0.000000   
34              Brasilia  0.000000        0.01           0.000000   
35            Bratislava  0.000000        0.00           0.000000   
36           Brazzaville  0.000000        0.00           0.000000   
37            Bridgetown  0.000000        0.00           0.000000   
38              Brussels  0.000000        0.00           0.000000   
39             Bucharest  0.000000        0.00           0.000000   
40              Budapest  0.000000        0.00           0.000000   
41          Buenos Aires  0.000000        0.00           0.000000   
42             Bujumbura  0.000000        0.00           0.000000   
43                 Cairo  0.000000        0.00           0.000000   
44              Canberra  0.000000        0.00           0.000000   
45               Caracas  0.000000        0.00           0.000000   
46              Castries  0.000000        0.00           0.000000   
47      Charlotte Amalie  0.000000        0.00           0.000000   
48              Chisinau  0.000000        0.00           0.000000   
49               Colombo  0.000000        0.00           0.000000   
50               Conakry  0.000000        0.00           0.000000   
51            Copenhagen  0.000000        0.00           0.000000   
52              Damascus  0.000000        0.00           0.000000   
53         Dar es Salaam  0.000000        0.00           0.000000   
54                 Dhaka  0.000000        0.00           0.000000   
55              Djibouti  0.000000        0.00           0.000000   
56                  Doha  0.000000        0.00           0.000000   
57        

In [92]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [93]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Capital Name']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
world_venues_sorted = pd.DataFrame(columns=columns)
world_venues_sorted['Capital Name'] = world_grouped['Capital Name']

for ind in np.arange(world_grouped.shape[0]):
    world_venues_sorted.iloc[ind, 1:] = return_most_common_venues(world_grouped.iloc[ind, :], num_top_venues)

world_venues_sorted.head()

Capital Name 1st Most Common Venue 2nd Most Common Venue  \
0    Abu Dhabi                  Café           Coffee Shop   
1        Abuja                  Park  Gym / Fitness Center   
2        Accra           Bus Station                 Hotel   
3  Addis Ababa            Restaurant             Hotel Bar   
4      Algiers                 Hotel                  Café   

       3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0  Middle Eastern Restaurant          Dessert Shop                Bakery   
1                Zoo Exhibit         Fishing Store               Exhibit   
2                 Restaurant        History Museum           Flea Market   
3         English Restaurant  Ethiopian Restaurant           Event Space   
4                 Restaurant          Burger Joint                 Plaza   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0          Burger Joint                 Hotel     Indian Restaurant   
1            Eye Doctor           Fabric Shop    Falafel Restaurant   
2      Asian Restaurant    Athletics & Sports               Theater   
3               Exhibit            Eye Doctor           Fabric Shop   
4     French Restaurant        History Museum  Fast Food Restaurant   

  9th Most Common Venue 10th Most Common Venue  
0    Turkish Restaurant     Chinese Restaurant  
1        Farmers Market   Fast Food Restaurant  
2                Market    Arts & Crafts Store  
3    Falafel Restaurant         Farmers Market  
4                 Diner            Coffee Shop

In [94]:
# set number of clusters: 6 continents
kclusters = 6

world_grouped_clustering = world_grouped.drop('Capital Name', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(world_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([1, 1, 1, 2, 1, 1, 1, 1, 1, 3], dtype=int32)

In [95]:
# add clustering labels
world_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

world_merged = df

# merge world_grouped with world_data to add latitude/longitude for each capital
world_merged = world_merged.join(world_venues_sorted.set_index('Capital Name'), on='Capital Name')
world_merged=world_merged.dropna()
world_merged['Cluster Labels']=world_merged['Cluster Labels'].astype(int)
world_merged['Capital Latitude']=world_merged['Capital Latitude'].astype(float)
world_merged['Capital Longitude']=world_merged['Capital Longitude'].astype(float)

world_merged.head()

Country Name Capital Name  Capital Latitude  Capital Longitude  \
0     Afghanistan        Kabul         34.516667          69.183333   
1   Aland Islands    Mariehamn         60.116667          19.900000   
2         Albania       Tirana         41.316667          19.816667   
3         Algeria      Algiers         36.750000           3.050000   
4  American Samoa    Pago Pago        -14.266667        -170.700000   

  Country Code Continent Name  Cluster Labels 1st Most Common Venue  \
0           AF           Asia               3                 Hotel   
1           AX         Europe               1           Supermarket   
2           AL         Europe               1                  Café   
3           DZ         Africa               1                 Hotel   
4           AS      Australia               1         National Park   

  2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
0         Shopping Mall            Campground                  Food   
1                 Trail           Flower Shop               Airport   
2    Italian Restaurant                 Hotel                   Bar   
3                  Café            Restaurant          Burger Joint   
4              Mountain            Food Court  Fast Food Restaurant   

           5th Most Common Venue 6th Most Common Venue  \
0                    Pizza Place         Design Studio   
1  Paper / Office Supplies Store  Gym / Fitness Center   
2                   Cocktail Bar           Coffee Shop   
3                          Plaza     French Restaurant   
4             Mexican Restaurant            Art Museum   

         7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
0                 Soccer Field     French Restaurant                Bakery   
1             Airport Terminal  Fast Food Restaurant     Fish & Chips Shop   
2  Eastern European Restaurant                Lounge            Restaurant   
3               History Museum  Fast Food Restaurant                 Diner   
4                Fishing Store          Fish Taverna           Fish Market   

  10th Most Common Venue  
0            Coffee Shop  
1    Filipino Restaurant  
2            Pizza Place  
3            Coffee Shop  
4      Fish & Chips Shop

In [96]:
# create map
map_clusters = folium.Map(location=[0,0], zoom_start=1)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(world_merged['Capital Latitude'], world_merged['Capital Longitude'], world_merged['Capital Name'], world_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

In [97]:
world_merged

Country Name         Capital Name  \
0                            Afghanistan                Kabul   
1                          Aland Islands            Mariehamn   
2                                Albania               Tirana   
3                                Algeria              Algiers   
4                         American Samoa            Pago Pago   
5                                Andorra     Andorra la Vella   
6                                 Angola               Luanda   
7                               Anguilla           The Valley   
8                    Antigua and Barbuda         Saint John’s   
9                              Argentina         Buenos Aires   
10                               Armenia              Yerevan   
11                                 Aruba           Oranjestad   
12                             Australia             Canberra   
13                               Austria               Vienna   
14                            Azerbaijan                 Baku   
15                               Bahamas               Nassau   
16                               Bahrain               Manama   
17                            Bangladesh                Dhaka   
18                              Barbados           Bridgetown   
19                               Belarus                Minsk   
20                               Belgium             Brussels   
21                                Belize             Belmopan   
22                                 Benin           Porto-Novo   
23                               Bermuda             Hamilton   
24                                Bhutan              Thimphu   
25                               Bolivia               La Paz   
26                Bosnia and Herzegovina             Sarajevo   
27                              Botswana             Gaborone   
28                                Brazil             Brasilia   
30                British Virgin Islands            Road Town   
31                     Brunei Darussalam  Bandar Seri Begawan   
32                              Bulgaria                Sofia   
33                          Burkina Faso          Ouagadougou   
34                               Burundi            Bujumbura   
35                              Cambodia           Phnom Penh   
36                              Cameroon              Yaounde   
37                                Canada               Ottawa   
38                            Cape Verde                Praia   
39                        Cayman Islands          George Town   
40              Central African Republic               Bangui   
41                                  Chad            N’Djamena   
42                                 Chile             Santiago   
43                                 China              Beijing   
44                      Christmas Island       The Settlement   
46                              Colombia               Bogota   
47                               Comoros               Moroni   
48                          Cook Islands               Avarua   
49                            Costa Rica             San Jose   
50                         Cote d’Ivoire         Yamoussoukro   
51                               Croatia               Zagreb   
52                                  Cuba               Havana   
53                              CuraÃ§ao           Willemstad   
54                                Cyprus              Nicosia   
55                        Czech Republic               Prague   
56      Democratic Republic of the Congo             Kinshasa   
57                               Denmark           Copenhagen   
58                              Djibouti             Djibouti   
59                              Dominica               Roseau   
60                    Dominican Republic        Santo Domingo   
61                               Ecuador                Quito   
62                                 Egypt                Cairo  